In [3]:
import numpy as np
from simsopt.geo import SurfaceRZFourier, CurveCWSFourier
from simsopt.field import Current, coils_via_symmetries, Coil


In [4]:
wout = 'input.final'
MAXITER = 2000 
ncoils = 2
order = 1 # order of dofs of cws curves
quadpoints = 300 #13 * order
ntheta = 50
nphi = 42
theta_linspace = np.linspace(0, 1, ntheta, endpoint=True)
phi_linspace = np.linspace(0, 1, nphi, endpoint=True)
# ext_via_normal_factor = 0.2565
ext_via_normal_factor = 0.1482

s = SurfaceRZFourier.from_vmec_input(wout, range="half period", quadpoints_theta=theta_linspace, quadpoints_phi=phi_linspace)#ntheta=ntheta, nphi=nphi)
phi_linspace_full = np.linspace(0, 1, int(nphi*2*s.nfp), endpoint=True)
s_full = SurfaceRZFourier.from_vmec_input(wout, range="full torus", quadpoints_theta=theta_linspace, quadpoints_phi=phi_linspace_full)#ntheta=ntheta, nphi=int(nphi*2*s.nfp))
# CREATE COIL WINDING SURFACE SURFACE
cws = SurfaceRZFourier.from_vmec_input(wout, range="half period", quadpoints_theta=theta_linspace, quadpoints_phi=phi_linspace)#ntheta=ntheta, nphi=nphi)
cws_full = SurfaceRZFourier.from_vmec_input(wout, range="full torus", quadpoints_theta=theta_linspace, quadpoints_phi=phi_linspace_full)#ntheta=ntheta, nphi=int(nphi*2*s.nfp))

cws.extend_via_normal(ext_via_normal_factor)
cws_full.extend_via_normal(ext_via_normal_factor)

# CREATE CURVES + COILS     
base_curves = []

curve_cws = CurveCWSFourier(
    mpol=cws.mpol,
    ntor=cws.ntor,
    idofs=cws.x,
    quadpoints=quadpoints,
    order=order,
    nfp=cws.nfp,
    stellsym=cws.stellsym,
)
angle = (0 + 0.5)*(2 * np.pi)/((2) * s.nfp * ncoils)
saddle_coil_dofs_inner = np.zeros(len(curve_cws.get_dofs()),)
saddle_coil_dofs_inner[2*order+3] = angle
saddle_coil_dofs_inner[2*order] = 1
saddle_coil_dofs_inner[2*order+5] = 1
curve_cws.set_dofs(saddle_coil_dofs_inner)
curve_cws.fix(0)
curve_cws.fix(2*order+2)
base_curves.append(curve_cws)
base_currents = Current(1)*1e5

# coils = coils_via_symmetries(base_curves, base_currents, s.nfp, True)
coils = [Coil(base_curves[0], base_currents)]

In [5]:
ax = s_full.plot(color="blue", close=True, show=False, engine="plotly", opacity=0.5)
ax.update_layout(showlegend=False)
cws_full.plot(ax=ax, color="lightblue", show=False, engine="plotly", close=True, opacity=0.5)
ax.update_layout(showlegend=False)
for coil in coils:
    coil.plot(ax=ax, color="green", show=False, engine="plotly", close=True)
# set box size
ax.update_layout(autosize=False, width=800, height=800)
# remove all bars 
ax.update_layout(showlegend=False)
ax.show()

In [6]:
s.nfp

5